# Building a song recommender


## Fire up GraphLab Create

In [6]:
import graphlab
graphlab.canvas.set_target('ipynb')

# Load music data

In [8]:
song_data = graphlab.SFrame('song_data.gl/')

# Explore data

Music data shows how many times a user listened to a song, as well as the details of the song.

In [19]:
song_data.show()

##Showing the most popular songs in the dataset

In [18]:
song_data['song'].show()

In [26]:
print len(song_data)
users = song_data['user_id'].unique()
print len(users)
songs = song_data['song_id'].unique()
print len(songs)
songs_byName = song_data['song'].unique()
print len(songs_byName)

1116609
66346
10000
9952


In [28]:
users_Kanye_West = song_data[song_data['artist'] == 'Kanye West']['user_id'].unique()
len(users_Kanye_West)

2522

In [29]:
users_Foo_Fighters = song_data[song_data['artist'] == 'Foo Fighters']['user_id'].unique()
len(users_Foo_Fighters)

2055

In [32]:
users_Taylor_Swift = song_data[song_data['artist'] == 'Taylor Swift']['user_id'].unique()
len(users_Taylor_Swift)

3246

In [33]:
users_Lady_GaGa = song_data[song_data['artist'] == 'Lady GaGa']['user_id'].unique()
len(users_Lady_GaGa)

2928

# groupby

In [41]:
artist_groupby = song_data.groupby(key_columns='artist', operations={'total_count': graphlab.aggregate.SUM('listen_count')})

In [49]:
artist_groupby.show()

In [50]:
artist_groupby.sort('total_count', ascending=False)

Columns:
	artist	str
	total_count	int

Rows: 3375

Data:
+------------------------+-------------+
|         artist         | total_count |
+------------------------+-------------+
|     Kings Of Leon      |    43218    |
|     Dwight Yoakam      |    40619    |
|         Björk          |    38889    |
|        Coldplay        |    35362    |
| Florence + The Machine |    33387    |
|     Justin Bieber      |    29715    |
|    Alliance Ethnik     |    26689    |
|      OneRepublic       |    25754    |
|         Train          |    25402    |
|     The Black Keys     |    22184    |
+------------------------+-------------+
[3375 rows x 2 columns]
Note: Only the head of the SFrame is printed.
You can use print_rows(num_rows=m, num_columns=n) to print more rows and columns.

In [51]:
artist_groupby.sort('total_count', ascending=True)

Columns:
	artist	str
	total_count	int

Rows: 3375

Data:
+-------------------------------+-------------+
|             artist            | total_count |
+-------------------------------+-------------+
|        William Tabbert        |      14     |
|         Reel Feelings         |      24     |
| Beyoncé feat. Bun B and Sl... |      26     |
|         Boggle Karaoke        |      30     |
|             Diplo             |      30     |
|         harvey summers        |      31     |
|             Nâdiya            |      36     |
|          Jody Bernal          |      38     |
|        Aneta Langerova        |      38     |
| Kanye West / Talib Kweli /... |      38     |
+-------------------------------+-------------+
[3375 rows x 2 columns]
Note: Only the head of the SFrame is printed.
You can use print_rows(num_rows=m, num_columns=n) to print more rows and columns.

In [83]:
artist_groupby[artist_groupby['artist'] == 'Kanye West'].head()

Columns:
	artist	str
	total_count	int

Rows: 1

Data:
+------------+-------------+
|   artist   | total_count |
+------------+-------------+
| Kanye West |     9992    |
+------------+-------------+
[1 rows x 2 columns]

In [84]:
artist_groupby[artist_groupby['artist'] == 'Taylor Swift'].head()

Columns:
	artist	str
	total_count	int

Rows: 1

Data:
+--------------+-------------+
|    artist    | total_count |
+--------------+-------------+
| Taylor Swift |    19376    |
+--------------+-------------+
[1 rows x 2 columns]

In [85]:
artist_groupby[artist_groupby['artist'] == 'Foo Fighters'].head()

Columns:
	artist	str
	total_count	int

Rows: 1

Data:
+--------------+-------------+
|    artist    | total_count |
+--------------+-------------+
| Foo Fighters |     9504    |
+--------------+-------------+
[1 rows x 2 columns]

In [86]:
artist_groupby[artist_groupby['artist'] == 'Lady GaGa'].head()

Columns:
	artist	str
	total_count	int

Rows: 1

Data:
+-----------+-------------+
|   artist  | total_count |
+-----------+-------------+
| Lady GaGa |    12224    |
+-----------+-------------+
[1 rows x 2 columns]

## Count number of unique users in the dataset

# Create a song recommender

In [52]:
train_data,test_data = song_data.random_split(.8,seed=0)

##Simple popularity-based recommender

In [53]:
popularity_model = graphlab.popularity_recommender.create(train_data,
                                                         user_id='user_id',
                                                         item_id='song')

PROGRESS: Recsys training: model = popularity
PROGRESS: Warning: Ignoring columns song_id, listen_count, title, artist;
PROGRESS:     To use one of these as a target column, set target = <column_name>
PROGRESS:     and use a method that allows the use of a target.
PROGRESS: Preparing data set.
PROGRESS:     Data has 893580 observations with 66085 users and 9952 items.
PROGRESS:     Data prepared in: 0.731567s
PROGRESS: 893580 observations to process; with 9952 unique items.


###Use the popularity model to make some predictions

A popularity model makes the same prediction for all users, so provides no personalization.

In [54]:
popularity_model.recommend(users=[users[0]])

Columns:
	user_id	str
	song	str
	score	float
	rank	int

Rows: 10

Data:
+-------------------------------+--------------------------------+--------+------+
|            user_id            |              song              | score  | rank |
+-------------------------------+--------------------------------+--------+------+
| 279292bb36dbfc7f505e36ebf0... |    Sehr kosmisch - Harmonia    | 4754.0 |  1   |
| 279292bb36dbfc7f505e36ebf0... |          Undo - Björk          | 4227.0 |  2   |
| 279292bb36dbfc7f505e36ebf0... | You're The One - Dwight Yoakam | 3781.0 |  3   |
| 279292bb36dbfc7f505e36ebf0... | Dog Days Are Over (Radio E...  | 3633.0 |  4   |
| 279292bb36dbfc7f505e36ebf0... |    Revelry - Kings Of Leon     | 3527.0 |  5   |
| 279292bb36dbfc7f505e36ebf0... | Horn Concerto No. 4 in E f...  | 3161.0 |  6   |
| 279292bb36dbfc7f505e36ebf0... |     Secrets - OneRepublic      | 3148.0 |  7   |
| 279292bb36dbfc7f505e36ebf0... |    Hey_ Soul Sister - Train    | 2538.0 |  8   |
| 279292bb36dbfc7f505e36ebf0... | Fireflies - Charttraxx Karaoke | 2532.0 |  9   |
| 279292bb36dbfc7f505e36ebf0... |       Tive Sim - Cartola       | 2521.0 |  10  |
+-------------------------------+--------------------------------+--------+------+
[10 rows x 4 columns]

## Build a song recommender with personalization

We now create a model that allows us to make personalized recommendations to each user. 

In [55]:
personalized_model = graphlab.item_similarity_recommender.create(train_data,
                                                                user_id='user_id',
                                                                item_id='song')

PROGRESS: Recsys training: model = item_similarity
PROGRESS: Warning: Ignoring columns song_id, listen_count, title, artist;
PROGRESS:     To use one of these as a target column, set target = <column_name>
PROGRESS:     and use a method that allows the use of a target.
PROGRESS: Preparing data set.
PROGRESS:     Data has 893580 observations with 66085 users and 9952 items.
PROGRESS:     Data prepared in: 0.757767s
PROGRESS: Computing item similarity statistics:
PROGRESS: Computing most similar items for 9952 items:
PROGRESS: +-----------------+-----------------+
PROGRESS: | Number of items | Elapsed Time    |
PROGRESS: +-----------------+-----------------+
PROGRESS: | 1000            | 1.39556         |
PROGRESS: | 2000            | 1.42954         |
PROGRESS: | 3000            | 1.46382         |
PROGRESS: | 4000            | 1.49692         |
PROGRESS: | 5000            | 1.52993         |
PROGRESS: | 6000            | 1.56179         |
PROGRESS: | 7000            | 1.59472         |

###Applying the personalized model to make song recommendations

As you can see, different users get different recommendations now.

In [56]:
personalized_model.recommend(users=[users[0]])

Columns:
	user_id	str
	song	str
	score	float
	rank	int

Rows: 10

Data:
+-------------------------------+--------------------------------+
|            user_id            |              song              |
+-------------------------------+--------------------------------+
| 279292bb36dbfc7f505e36ebf0... | Riot In Cell Block Number ...  |
| 279292bb36dbfc7f505e36ebf0... | Sei Lá Mangueira - Elizeth...  |
| 279292bb36dbfc7f505e36ebf0... |      The Stallion - Ween       |
| 279292bb36dbfc7f505e36ebf0... |        Rain - Subhumans        |
| 279292bb36dbfc7f505e36ebf0... | West One (Shine On Me) - T...  |
| 279292bb36dbfc7f505e36ebf0... | Back Against The Wall - Ca...  |
| 279292bb36dbfc7f505e36ebf0... | Life Less Frightening - Ri...  |
| 279292bb36dbfc7f505e36ebf0... | A Beggar On A Beach Of Gol...  |
| 279292bb36dbfc7f505e36ebf0... | Audience Of One - Rise Against |
| 279292bb36dbfc7f505e36ebf0... | Blame It On The Boogie - T...  |
+-------------------------------+--------------------------------+
+-----------------+------+
|      score      | rank |
+-----------------+------+
|      0.0375     |  1   |
| 0.0331632653061 |  2   |
| 0.0322580645161 |  3   |
| 0.0314159292035 |  4   |
| 0.0307390385081 |  5   |
| 0.0301204819277 |  6   |
| 0.0284431137725 |  7   |
| 0.0230024907156 |  8   |
| 0.0193938442211 |  9   |
| 0.0190677966102 |  10  |
+-----------------+------+
[10 rows x 4 columns]

###We can also apply the model to find similar songs to any song in the dataset

In [57]:
personalized_model.get_similar_items(['With Or Without You - U2'])

PROGRESS: Getting similar items completed in 0.009797


Columns:
	song	str
	similar	str
	score	float
	rank	int

Rows: 10

Data:
+--------------------------+-------------------------------+-----------------+
|           song           |            similar            |      score      |
+--------------------------+-------------------------------+-----------------+
| With Or Without You - U2 | I Still Haven't Found What... | 0.0428571428571 |
| With Or Without You - U2 | Hold Me_ Thrill Me_ Kiss M... |  0.033734939759 |
| With Or Without You - U2 |    Window In The Skies - U2   | 0.0328358208955 |
| With Or Without You - U2 |          Vertigo - U2         | 0.0300751879699 |
| With Or Without You - U2 |   Sunday Bloody Sunday - U2   | 0.0271317829457 |
| With Or Without You - U2 |            Bad - U2           | 0.0251798561151 |
| With Or Without You - U2 |     A Day Without Me - U2     | 0.0237154150198 |
| With Or Without You - U2 | Another Time Another Place... |  0.020325203252 |
| With Or Without You - U2 |          Walk On - U2         |  0.020202020202 |
| With Or Without You - U2 |     Get On Your Boots - U2    | 0.0196850393701 |
+--------------------------+-------------------------------+-----------------+
+------+
| rank |
+------+
|  1   |
|  2   |
|  3   |
|  4   |
|  5   |
|  6   |
|  7   |
|  8   |
|  9   |
|  10  |
+------+
[10 rows x 4 columns]

In [58]:
personalized_model.get_similar_items(['Chan Chan (Live) - Buena Vista Social Club'])

PROGRESS: Getting similar items completed in 0.003


Columns:
	song	str
	similar	str
	score	float
	rank	int

Rows: 10

Data:
+-------------------------------+--------------------------------+
|              song             |            similar             |
+-------------------------------+--------------------------------+
| Chan Chan (Live) - Buena V... | Murmullo - Buena Vista Soc...  |
| Chan Chan (Live) - Buena V... | La Bayamesa - Buena Vista ...  |
| Chan Chan (Live) - Buena V... | Amor de Loca Juventud - Bu...  |
| Chan Chan (Live) - Buena V... |   Diferente - Gotan Project    |
| Chan Chan (Live) - Buena V... |       Mistica - Orishas        |
| Chan Chan (Live) - Buena V... | Hotel California - Gipsy Kings |
| Chan Chan (Live) - Buena V... |     Nací Orishas - Orishas     |
| Chan Chan (Live) - Buena V... |    Le Moulin - Yann Tiersen    |
| Chan Chan (Live) - Buena V... |     Gitana - Willie Colon      |
| Chan Chan (Live) - Buena V... |    Criminal - Gotan Project    |
+-------------------------------+--------------------------------+
+-----------------+------+
|      score      | rank |
+-----------------+------+
|  0.188118811881 |  1   |
|  0.187192118227 |  2   |
|  0.184834123223 |  3   |
| 0.0214592274678 |  4   |
| 0.0205761316872 |  5   |
|  0.019305019305 |  6   |
| 0.0191570881226 |  7   |
| 0.0187969924812 |  8   |
| 0.0187969924812 |  9   |
|  0.018779342723 |  10  |
+-----------------+------+
[10 rows x 4 columns]

#Quantitative comparison between the models

We now formally compare the popularity and the personalized models using precision-recall curves. 

In [59]:
%matplotlib inline
model_performance = graphlab.recommender.util.compare_models(test_data,
                                                            [popularity_model,personalized_model],
                                                            user_sample=0.05)

compare_models: using 2931 users to estimate model performance
PROGRESS: Evaluate model M0
PROGRESS: recommendations finished on 1000/2931 queries. users per second: 17972
PROGRESS: recommendations finished on 2000/2931 queries. users per second: 23228.3

Precision and recall summary statistics by cutoff
+--------+-----------------+------------------+
| cutoff |  mean_precision |   mean_recall    |
+--------+-----------------+------------------+
|   1    | 0.0266120777892 | 0.00677255096395 |
|   2    | 0.0255885363357 | 0.0136618366659  |
|   3    | 0.0237689070852 | 0.0191374018907  |
|   4    | 0.0213237802798 |  0.022423171809  |
|   5    | 0.0195837598089 | 0.0247524301772  |
|   6    | 0.0184806095758 | 0.0274010836959  |
|   7    | 0.0175951649851 |  0.03085839158   |
|   8    | 0.0167178437393 | 0.0332739827366  |
|   9    | 0.0156563933432 | 0.0348637336355  |
|   10   | 0.0150801774139 | 0.0382748615348  |
+--------+-----------------+------------------+
[10 rows x 3 columns]


[WARNING] Model trained without a target. Skipping RMSE computation.



PROGRESS: Evaluate model M1
PROGRESS: recommendations finished on 1000/2931 queries. users per second: 1609.33
PROGRESS: recommendations finished on 2000/2931 queries. users per second: 1648.49

Precision and recall summary statistics by cutoff
+--------+-----------------+-----------------+
| cutoff |  mean_precision |   mean_recall   |
+--------+-----------------+-----------------+
|   1    |  0.199931763903 |  0.06392228502  |
|   2    |  0.164790174002 | 0.0988530141407 |
|   3    |  0.14329580348  |  0.123730932954 |
|   4    |  0.129819174343 |  0.145074688331 |
|   5    |  0.11736608666  |  0.161249834879 |
|   6    |  0.107528716024 |  0.176215673847 |
|   7    | 0.0995272213287 |  0.190054760523 |
|   8    | 0.0930996247015 |  0.203053579816 |
|   9    | 0.0882899275939 |  0.215708205508 |
|   10   |  0.084680996247 |  0.227440758656 |
+--------+-----------------+-----------------+
[10 rows x 3 columns]


[WARNING] Model trained without a target. Skipping RMSE computation.


The curve shows that the personalized model provides much better performance. 

In [75]:
subset_test_users = test_data['user_id'].unique()[0:10000]
subset_testuser_recommend_song = personalized_model.recommend(subset_test_users,k=1)

PROGRESS: recommendations finished on 1000/10000 queries. users per second: 1636.35
PROGRESS: recommendations finished on 2000/10000 queries. users per second: 1676.91
PROGRESS: recommendations finished on 3000/10000 queries. users per second: 1683
PROGRESS: recommendations finished on 4000/10000 queries. users per second: 1698.37
PROGRESS: recommendations finished on 5000/10000 queries. users per second: 1698.67
PROGRESS: recommendations finished on 6000/10000 queries. users per second: 1703.17
PROGRESS: recommendations finished on 7000/10000 queries. users per second: 1698.23
PROGRESS: recommendations finished on 8000/10000 queries. users per second: 1699.81
PROGRESS: recommendations finished on 9000/10000 queries. users per second: 1702.11
PROGRESS: recommendations finished on 10000/10000 queries. users per second: 1700.17


In [76]:
subset_testuser_recommend_song.show()

# get the most recommended song by personization recommender.

In [78]:
most_recommended_song_by_personization_model = subset_testuser_recommend_song.groupby(key_columns='song', operations={'total_count': graphlab.aggregate.COUNT()})

In [80]:
most_recommended_song_by_personization_model.sort('total_count', ascending=False)

Columns:
	song	str
	total_count	int

Rows: 3144

Data:
+--------------------------------+-------------+
|              song              | total_count |
+--------------------------------+-------------+
|          Undo - Björk          |     432     |
|     Secrets - OneRepublic      |     373     |
|    Revelry - Kings Of Leon     |     235     |
| You're The One - Dwight Yoakam |     163     |
| Fireflies - Charttraxx Karaoke |     118     |
|    Hey_ Soul Sister - Train    |     106     |
| Horn Concerto No. 4 in E f...  |      92     |
|    Sehr kosmisch - Harmonia    |      86     |
| OMG - Usher featuring will...  |      64     |
|    The Scientist - Coldplay    |      47     |
+--------------------------------+-------------+
[3144 rows x 2 columns]
Note: Only the head of the SFrame is printed.
You can use print_rows(num_rows=m, num_columns=n) to print more rows and columns.

In [82]:
most_recommended_song_by_personization_model.sort('total_count', ascending=True)

Columns:
	song	str
	total_count	int

Rows: 3144

Data:
+-------------------------------+-------------+
|              song             | total_count |
+-------------------------------+-------------+
|       Arco Arena - Cake       |      1      |
| The Warrior's Code - Dropk... |      1      |
|   Anything New - Digitalism   |      1      |
| Fast Forward To 2012 (Albu... |      1      |
|  Wish You Were Here - Incubus |      1      |
|      Change - Blind Melon     |      1      |
|        Get:On - Moguai        |      1      |
| Dream About Flying - Alexi... |      1      |
| Get Me Away From Here_ I'm... |      1      |
|      Elysium - Portishead     |      1      |
+-------------------------------+-------------+
[3144 rows x 2 columns]
Note: Only the head of the SFrame is printed.
You can use print_rows(num_rows=m, num_columns=n) to print more rows and columns.